In [1]:
from keras.models import Sequential
from keras import layers
import numpy as np
from six.moves import range

/usr/local/lib/python3.5/dist-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
Using TensorFlow backend.


# Parameters Config

In [2]:
class colors:
    ok = '\033[92m'
    fail = '\033[91m'
    close = '\033[0m'

In [3]:
TRAINING_SIZE = 120000
DIGITS = 3
REVERSE = False
MAXLEN = DIGITS + 1 + DIGITS
chars = '0123456789- '
RNN = layers.LSTM
HIDDEN_SIZE = 128
BATCH_SIZE = 128
LAYERS = 1

In [4]:
class CharacterTable(object):
    def __init__(self, chars):
        self.chars = sorted(set(chars))
        self.char_indices = dict((c, i) for i, c in enumerate(self.chars))
        self.indices_char = dict((i, c) for i, c in enumerate(self.chars))
    
    # one-hot encoder
    def encode(self, C, num_rows):
        x = np.zeros((num_rows, len(self.chars)))
        for i, c in enumerate(C):
            x[i, self.char_indices[c]] = 1
        return x
    
    def decode(self, x, calc_argmax=True):
        if calc_argmax:
            x = x.argmax(axis=-1)
        return "".join(self.indices_char[i] for i in x)

In [5]:
ctable = CharacterTable(chars)

In [6]:
ctable.indices_char

{0: ' ',
 1: '-',
 2: '0',
 3: '1',
 4: '2',
 5: '3',
 6: '4',
 7: '5',
 8: '6',
 9: '7',
 10: '8',
 11: '9'}

# Data Generation

In [7]:
questions = []
expected = []
seen = set()
print('Generating data...')
while len(questions) < TRAINING_SIZE:
    f = lambda: int(''.join(np.random.choice(list('0123456789')) for i in range(np.random.randint(1, DIGITS + 1))))
    a, b = f(), f()
    key = tuple(sorted((a, b)))
    if key in seen:
        continue
    seen.add(key)
    q = '{}-{}'.format(a, b)
    query = q + ' ' * (MAXLEN - len(q))
    ans = str(a - b)
    ans += ' ' * (DIGITS + 2 - len(ans))
    if REVERSE:
        query = query[::-1]
    questions.append(query)
    expected.append(ans)
print('Total addition questions:', len(questions))

Generating data...
Total addition questions: 120000


In [ ]:
print(questions[:5], expected[:5])

# Processing

In [8]:
print('Vectorization...')
x = np.zeros((len(questions), MAXLEN, len(chars)), dtype=np.bool)
y = np.zeros((len(expected), DIGITS + 2, len(chars)), dtype=np.bool)
for i, sentence in enumerate(questions):
    x[i] = ctable.encode(sentence, MAXLEN)
for i, sentence in enumerate(expected):
    y[i] = ctable.encode(sentence, DIGITS + 2)

Vectorization...


In [9]:
indices = np.arange(len(y))
np.random.shuffle(indices)
x = x[indices]
y = y[indices]

# train_test_split
train_x = x[:20000]
train_y = y[:20000]
test_x = x[20000:]
test_y = y[20000:]

split_at = len(train_x) - len(train_x) // 10
(x_train, x_val) = train_x[:split_at], train_x[split_at:]
(y_train, y_val) = train_y[:split_at], train_y[split_at:]

print('Training Data:')
print(x_train.shape)
print(y_train.shape)

print('Validation Data:')
print(x_val.shape)
print(y_val.shape)

print('Testing Data:')
print(test_x.shape)
print(test_y.shape)

Training Data:
(18000, 7, 12)
(18000, 5, 12)
Validation Data:
(2000, 7, 12)
(2000, 5, 12)
Testing Data:
(100000, 7, 12)
(100000, 5, 12)


In [ ]:
print("input: ", x_train[:3], '\n\n', "label: ", y_train[:3])

# Build Model

In [10]:
print('Build model...')
model = Sequential()
model.add(RNN(HIDDEN_SIZE, input_shape=(MAXLEN, len(chars))))
model.add(layers.RepeatVector(DIGITS + 2))
for _ in range(LAYERS):
    model.add(RNN(HIDDEN_SIZE, return_sequences=True))

model.add(layers.TimeDistributed(layers.Dense(len(chars))))
model.add(layers.Activation('softmax'))
model.compile(loss='categorical_crossentropy',
              optimizer='adam',
              metrics=['accuracy'])
model.summary()

Build model...
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
lstm_1 (LSTM)                (None, 128)               72192     
_________________________________________________________________
repeat_vector_1 (RepeatVecto (None, 5, 128)            0         
_________________________________________________________________
lstm_2 (LSTM)                (None, 5, 128)            131584    
_________________________________________________________________
time_distributed_1 (TimeDist (None, 5, 12)             1548      
_________________________________________________________________
activation_1 (Activation)    (None, 5, 12)             0         
Total params: 205,324
Trainable params: 205,324
Non-trainable params: 0
_________________________________________________________________


# Training

In [11]:
for iteration in range(150):
    print()
    print('-' * 50)
    print('Iteration', iteration)
    model.fit(x_train, y_train,
              batch_size=BATCH_SIZE,
              epochs=1,
              validation_data=(x_val, y_val))
    for i in range(10):
        ind = np.random.randint(0, len(x_val))
        rowx, rowy = x_val[np.array([ind])], y_val[np.array([ind])]
        preds = model.predict_classes(rowx, verbose=0)
        q = ctable.decode(rowx[0])
        correct = ctable.decode(rowy[0])
        guess = ctable.decode(preds[0], calc_argmax=False)
        print('Q', q[::-1] if REVERSE else q, end=' ')
        print('T', correct, end=' ')
        if correct == guess:
            print(colors.ok + '☑' + colors.close, end=' ')
        else:
            print(colors.fail + '☒' + colors.close, end=' ')
        print(guess)


--------------------------------------------------
Iteration 0
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 3s 161us/step - loss: 1.8496 - acc: 0.3927 - val_loss: 1.6206 - val_acc: 0.4583
Q 26-319  T -293  ☒ -30  
Q 827-452 T 375   ☒ -10  
Q 37-971  T -934  ☒ -30  
Q 534-386 T 148   ☒ -30  
Q 764-525 T 239   ☒ -30  
Q 99-9    T 90    ☒ -30  
Q 722-73  T 649   ☒ -10  
Q 981-682 T 299   ☒ -10  
Q 249-232 T 17    ☒ -10  
Q 360-4   T 356   ☒ -10  

--------------------------------------------------
Iteration 1
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 2s 97us/step - loss: 1.5274 - acc: 0.4618 - val_loss: 1.4749 - val_acc: 0.4629
Q 495-756 T -261  ☒ -20  
Q 788-471 T 317   ☒ -20  
Q 71-326  T -255  ☒ -22  
Q 762-15  T 747   ☒ 11   
Q 356-243 T 113   ☒ -21  
Q 600-641 T -41   ☒ -21  
Q 439-17  T 422   ☒ -2   
Q 964-841 T 123   ☒ -20  
Q 34-362  T -328  ☒ -12  
Q 805-6

18000/18000 [==============================] - 2s 91us/step - loss: 1.0527 - acc: 0.6178 - val_loss: 1.0561 - val_acc: 0.6131
Q 71-326  T -255  ☒ -281 
Q 262-941 T -679  ☒ -688 
Q 8-833   T -825  ☒ -811 
Q 91-613  T -522  ☒ -533 
Q 140-743 T -603  ☒ -681 
Q 604-862 T -258  ☒ -279 
Q 360-22  T 338   ☒ 333  
Q 436-358 T 78    ☒ 11   
Q 951-173 T 778   ☒ 719  
Q 690-536 T 154   ☒ 123  

--------------------------------------------------
Iteration 15
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 2s 90us/step - loss: 1.0371 - acc: 0.6233 - val_loss: 1.0351 - val_acc: 0.6258
Q 546-29  T 517   ☒ 433  
Q 157-670 T -513  ☒ -547 
Q 88-73   T 15    ☒ 1    
Q 93-919  T -826  ☒ -839 
Q 181-52  T 129   ☒ 15   
Q 647-328 T 319   ☒ 333  
Q 827-452 T 375   ☒ 367  
Q 71-464  T -393  ☒ -337 
Q 73-541  T -468  ☒ -487 
Q 243-73  T 170   ☒ 177  

--------------------------------------------------
Iteration 16
Train on 18000 samples, validate on 200

18000/18000 [==============================] - 2s 91us/step - loss: 0.7946 - acc: 0.7080 - val_loss: 0.8218 - val_acc: 0.6941
Q 754-895 T -141  ☒ -146 
Q 10-190  T -180  ☒ -98  
Q 49-914  T -865  ☑ -865 
Q 66-200  T -134  ☒ -136 
Q 99-502  T -403  ☒ -415 
Q 482-92  T 390   ☒ 386  
Q 604-862 T -258  ☒ -266 
Q 803-224 T 579   ☒ 569  
Q 71-326  T -255  ☒ -261 
Q 648-53  T 595   ☒ 611  

--------------------------------------------------
Iteration 29
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 2s 90us/step - loss: 0.7844 - acc: 0.7124 - val_loss: 0.8026 - val_acc: 0.7000
Q 943-108 T 835   ☒ 802  
Q 276-755 T -479  ☒ -483 
Q 764-101 T 663   ☒ 645  
Q 738-382 T 356   ☒ 367  
Q 955-72  T 883   ☒ 894  
Q 13-682  T -669  ☒ -676 
Q 59-80   T -21   ☒ -18  
Q 722-73  T 649   ☒ 656  
Q 12-619  T -607  ☒ -606 
Q 484-746 T -262  ☒ -266 

--------------------------------------------------
Iteration 30
Train on 18000 samples, validate on 200

18000/18000 [==============================] - 2s 90us/step - loss: 0.6205 - acc: 0.7769 - val_loss: 0.6862 - val_acc: 0.7387
Q 227-458 T -231  ☒ -227 
Q 296-747 T -451  ☒ -458 
Q 821-205 T 616   ☒ 612  
Q 92-830  T -738  ☒ -730 
Q 30-188  T -158  ☒ -166 
Q 641-840 T -199  ☒ -109 
Q 649-89  T 560   ☒ 553  
Q 23-268  T -245  ☒ -252 
Q 737-237 T 500   ☒ 597  
Q 378-612 T -234  ☒ -235 

--------------------------------------------------
Iteration 43
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 2s 90us/step - loss: 0.6108 - acc: 0.7810 - val_loss: 0.6958 - val_acc: 0.7437
Q 72-544  T -472  ☒ -475 
Q 440-94  T 346   ☒ 355  
Q 340-627 T -287  ☒ -383 
Q 94-70   T 24    ☒ 11   
Q 931-0   T 931   ☒ 922  
Q 36-121  T -85   ☒ -88  
Q 666-5   T 661   ☒ 653  
Q 80-725  T -645  ☒ -643 
Q 456-858 T -402  ☒ -401 
Q 43-88   T -45   ☒ -43  

--------------------------------------------------
Iteration 44
Train on 18000 samples, validate on 200

18000/18000 [==============================] - 2s 91us/step - loss: 0.3244 - acc: 0.8941 - val_loss: 0.3829 - val_acc: 0.8588
Q 558-397 T 161   ☒ 168  
Q 17-504  T -487  ☑ -487 
Q 184-501 T -317  ☑ -317 
Q 1-149   T -148  ☒ -147 
Q 438-661 T -223  ☒ -213 
Q 614-41  T 573   ☒ 572  
Q 714-97  T 617   ☒ 628  
Q 506-84  T 422   ☑ 422  
Q 499-47  T 452   ☒ 442  
Q 238-837 T -599  ☑ -599 

--------------------------------------------------
Iteration 57
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 2s 90us/step - loss: 0.3077 - acc: 0.9019 - val_loss: 0.3740 - val_acc: 0.8605
Q 723-92  T 631   ☑ 631  
Q 648-53  T 595   ☒ 585  
Q 234-742 T -508  ☑ -508 
Q 71-326  T -255  ☑ -255 
Q 46-980  T -934  ☒ -924 
Q 238-840 T -602  ☑ -602 
Q 733-18  T 715   ☑ 715  
Q 261-39  T 222   ☒ 223  
Q 628-590 T 38    ☒ 43   
Q 157-719 T -562  ☑ -562 

--------------------------------------------------
Iteration 58
Train on 18000 samples, validate on 200

...

18000/18000 [==============================] - 2s 90us/step - loss: 0.0744 - acc: 0.9838 - val_loss: 0.1519 - val_acc: 0.9490
Q 809-64  T 745   ☑ 745  
Q 186-737 T -551  ☑ -551 
Q 468-547 T -79   ☑ -79  
Q 91-130  T -39   ☒ -49  
Q 953-257 T 696   ☑ 696  
Q 998-388 T 610   ☒ 600  
Q 785-86  T 699   ☒ 799  
Q 496-849 T -353  ☑ -353 
Q 621-7   T 614   ☑ 614  
Q 456-858 T -402  ☑ -402 

--------------------------------------------------
Iteration 85
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 2s 90us/step - loss: 0.1154 - acc: 0.9690 - val_loss: 0.2972 - val_acc: 0.9027
Q 940-97  T 843   ☑ 843  
Q 78-515  T -437  ☑ -437 
Q 52-4    T 48    ☒ 40   
Q 180-441 T -261  ☑ -261 
Q 201-98  T 103   ☑ 103  
Q 414-639 T -225  ☑ -225 
Q 35-284  T -249  ☑ -249 
Q 99-85   T 14    ☒ 13   
Q 322-68  T 254   ☑ 254  
Q 55-964  T -909  ☑ -909 

--------------------------------------------------
Iteration 86
Train on 18000 samples, validate on 200

18000/18000 [==============================] - 2s 91us/step - loss: 0.0477 - acc: 0.9904 - val_loss: 0.1296 - val_acc: 0.9570
Q 42-82   T -40   ☒ -41  
Q 570-4   T 566   ☑ 566  
Q 32-290  T -258  ☑ -258 
Q 674-423 T 251   ☑ 251  
Q 803-224 T 579   ☒ 580  
Q 535-339 T 196   ☒ 296  
Q 179-32  T 147   ☑ 147  
Q 262-535 T -273  ☑ -273 
Q 504-72  T 432   ☑ 432  
Q 931-54  T 877   ☑ 877  

--------------------------------------------------
Iteration 99
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 2s 91us/step - loss: 0.0439 - acc: 0.9918 - val_loss: 0.1212 - val_acc: 0.9578
Q 583-669 T -86   ☑ -86  
Q 89-148  T -59   ☒ -69  
Q 7-508   T -501  ☑ -501 
Q 186-384 T -198  ☑ -198 
Q 36-638  T -602  ☑ -602 
Q 960-4   T 956   ☑ 956  
Q 66-924  T -858  ☑ -858 
Q 819-835 T -16   ☑ -16  
Q 640-78  T 562   ☑ 562  
Q 97-438  T -341  ☑ -341 

--------------------------------------------------
Iteration 100
Train on 18000 samples, validate on 20

18000/18000 [==============================] - 2s 91us/step - loss: 0.0258 - acc: 0.9967 - val_loss: 0.1137 - val_acc: 0.9620
Q 824-701 T 123   ☑ 123  
Q 24-437  T -413  ☑ -413 
Q 18-323  T -305  ☑ -305 
Q 274-155 T 119   ☑ 119  
Q 757-449 T 308   ☑ 308  
Q 22-854  T -832  ☑ -832 
Q 273-909 T -636  ☑ -636 
Q 298-854 T -556  ☑ -556 
Q 569-83  T 486   ☑ 486  
Q 233-43  T 190   ☑ 190  

--------------------------------------------------
Iteration 113
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 2s 91us/step - loss: 0.0257 - acc: 0.9965 - val_loss: 0.1152 - val_acc: 0.9595
Q 184-215 T -31   ☑ -31  
Q 824-0   T 824   ☑ 824  
Q 99-427  T -328  ☑ -328 
Q 74-46   T 28    ☒ 27   
Q 92-764  T -672  ☑ -672 
Q 728-96  T 632   ☑ 632  
Q 53-493  T -440  ☑ -440 
Q 795-298 T 497   ☑ 497  
Q 432-62  T 370   ☑ 370  
Q 105-603 T -498  ☑ -498 

--------------------------------------------------
Iteration 114
Train on 18000 samples, validate on 2

18000/18000 [==============================] - 2s 91us/step - loss: 0.0221 - acc: 0.9973 - val_loss: 0.1056 - val_acc: 0.9652
Q 602-263 T 339   ☑ 339  
Q 328-56  T 272   ☑ 272  
Q 75-566  T -491  ☑ -491 
Q 63-694  T -631  ☑ -631 
Q 193-189 T 4     ☒ 2    
Q 342-78  T 264   ☑ 264  
Q 68-173  T -105  ☑ -105 
Q 621-73  T 548   ☑ 548  
Q 51-704  T -653  ☑ -653 
Q 95-939  T -844  ☒ -845 

--------------------------------------------------
Iteration 127
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 2s 91us/step - loss: 0.0181 - acc: 0.9983 - val_loss: 0.1030 - val_acc: 0.9673
Q 729-909 T -180  ☑ -180 
Q 73-32   T 41    ☒ 31   
Q 335-824 T -489  ☑ -489 
Q 91-812  T -721  ☑ -721 
Q 93-364  T -271  ☑ -271 
Q 81-660  T -579  ☑ -579 
Q 810-20  T 790   ☑ 790  
Q 881-993 T -112  ☑ -112 
Q 729-59  T 670   ☒ 660  
Q 48-817  T -769  ☑ -769 

--------------------------------------------------
Iteration 128
Train on 18000 samples, validate on 2

18000/18000 [==============================] - 2s 91us/step - loss: 0.0186 - acc: 0.9977 - val_loss: 0.1121 - val_acc: 0.9622
Q 170-65  T 105   ☑ 105  
Q 866-390 T 476   ☑ 476  
Q 112-621 T -509  ☒ -519 
Q 927-916 T 11    ☒ 3    
Q 644-712 T -68   ☑ -68  
Q 882-145 T 737   ☑ 737  
Q 762-474 T 288   ☑ 288  
Q 584-535 T 49    ☑ 49   
Q 410-600 T -190  ☑ -190 
Q 418-952 T -534  ☑ -534 

--------------------------------------------------
Iteration 141
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 2s 91us/step - loss: 0.0141 - acc: 0.9989 - val_loss: 0.1057 - val_acc: 0.9663
Q 9-59    T -50   ☒ -59  
Q 157-296 T -139  ☑ -139 
Q 540-949 T -409  ☑ -409 
Q 154-621 T -467  ☑ -467 
Q 453-513 T -60   ☑ -60  
Q 94-70   T 24    ☒ 13   
Q 175-234 T -59   ☑ -59  
Q 184-69  T 115   ☑ 115  
Q 781-1   T 780   ☑ 780  
Q 748-373 T 375   ☑ 375  

--------------------------------------------------
Iteration 142
Train on 18000 samples, validate on 2

In [ ]:
print("MSG : Prediction")
test_x = ["555+275", "860+7  ", "340+29 "]
test_y = ["830 ", "867 ", "369 "]
x = np.zeros((len(test_x), MAXLEN, len(chars)), dtype=np.bool)
y = np.zeros((len(test_y), DIGITS + 2, len(chars)), dtype=np.bool)
for j, (i, c) in enumerate(zip(test_x, test_y)):
    x[j] = ctable.encode(i, MAXLEN)
    y[j] = ctable.encode(c, DIGITS + 2)

# Validation

In [12]:
right = 0
preds = model.predict_classes(test_x, verbose=0)
for i in range(len(preds)):
    q = ctable.decode(test_x[i])
    correct = ctable.decode(test_y[i])
    guess = ctable.decode(preds[i], calc_argmax=False)
    print('Q', q[::-1] if REVERSE else q, end=' ')
    print('T', correct, end=' ')
    if correct == guess:
        print(colors.ok + '☑' + colors.close, end=' ')
        right += 1
    else:
        print(colors.fail + '☒' + colors.close, end=' ')
    print(guess)
print("MSG : Accuracy is {}".format(right / len(preds)))

Q 999-529 T 470   ☑ 470  
Q 1-348   T -347  ☑ -347 
Q 604-764 T -160  ☑ -160 
Q 68-162  T -94   ☒ -95  
Q 271-24  T 247   ☑ 247  
Q 463-541 T -78   ☑ -78  
Q 311-32  T 279   ☑ 279  
Q 667-457 T 210   ☒ 200  
Q 21-93   T -72   ☒ -71  
Q 306-5   T 301   ☑ 301  
Q 481-122 T 359   ☒ 369  
Q 16-730  T -714  ☑ -714 
Q 541-89  T 452   ☑ 452  
Q 953-21  T 932   ☑ 932  
Q 20-125  T -105  ☑ -105 
Q 699-0   T 699   ☑ 699  
Q 200-330 T -130  ☑ -130 
Q 8-915   T -907  ☑ -907 
Q 327-91  T 236   ☑ 236  
Q 31-745  T -714  ☑ -714 
Q 969-29  T 940   ☑ 940  
Q 2-900   T -898  ☑ -898 
Q 129-20  T 109   ☑ 109  
Q 343-101 T 242   ☑ 242  
Q 3-448   T -445  ☑ -445 
Q 290-96  T 194   ☑ 194  
Q 19-250  T -231  ☑ -231 
Q 147-17  T 130   ☑ 130  
Q 20-208  T -188  ☑ -188 
Q 981-810 T 171   ☑ 171  
Q 877-900 T -23   ☒ -33  
Q 97-557  T -460  ☑ -460 
Q 144-19  T 125   ☑ 125  
Q 255-89  T 166   ☑ 166  
Q 257-48  T 209   ☑ 209  
Q 15-764  T -749  ☑ -749 
Q 998-66  T 932   ☑ 932  
Q 77-247  T -170  ☑ -170 
Q 83-0    T 

Q 46-770  T -724  ☑ -724 
Q 423-809 T -386  ☑ -386 
Q 869-23  T 846   ☑ 846  
Q 58-98   T -40   ☒ -30  
Q 37-372  T -335  ☑ -335 
Q 31-228  T -197  ☑ -197 
Q 400-792 T -392  ☒ -393 
Q 945-96  T 849   ☑ 849  
Q 18-738  T -720  ☑ -720 
Q 563-3   T 560   ☑ 560  
Q 401-46  T 355   ☑ 355  
Q 920-173 T 747   ☑ 747  
Q 62-39   T 23    ☒ 24   
Q 216-48  T 168   ☑ 168  
Q 97-893  T -796  ☑ -796 
Q 20-6    T 14    ☒ 13   
Q 161-993 T -832  ☒ -822 
Q 369-787 T -418  ☑ -418 
Q 84-956  T -872  ☑ -872 
Q 792-496 T 296   ☑ 296  
Q 195-51  T 144   ☒ 134  
Q 742-775 T -33   ☑ -33  
Q 56-953  T -897  ☑ -897 
Q 929-27  T 902   ☑ 902  
Q 515-150 T 365   ☑ 365  
Q 80-993  T -913  ☒ -903 
Q 4-321   T -317  ☑ -317 
Q 198-0   T 198   ☑ 198  
Q 916-101 T 815   ☑ 815  
Q 272-131 T 141   ☒ 131  
Q 822-82  T 740   ☑ 740  
Q 703-56  T 647   ☑ 647  
Q 48-640  T -592  ☑ -592 
Q 950-998 T -48   ☑ -48  
Q 547-51  T 496   ☑ 496  
Q 469-439 T 30    ☒ 20   
Q 1-88    T -87   ☒ -97  
Q 972-102 T 870   ☑ 870  
Q 29-209  T 

Q 479-747 T -268  ☑ -268 
Q 689-226 T 463   ☑ 463  
Q 653-662 T -9    ☒ -1   
Q 215-56  T 159   ☒ 169  
Q 636-20  T 616   ☑ 616  
Q 732-1   T 731   ☑ 731  
Q 593-35  T 558   ☑ 558  
Q 77-804  T -727  ☑ -727 
Q 269-90  T 179   ☒ 189  
Q 626-704 T -78   ☑ -78  
Q 803-382 T 421   ☑ 421  
Q 25-612  T -587  ☑ -587 
Q 876-43  T 833   ☑ 833  
Q 845-67  T 778   ☑ 778  
Q 634-206 T 428   ☑ 428  
Q 712-21  T 691   ☑ 691  
Q 259-55  T 204   ☑ 204  
Q 401-34  T 367   ☑ 367  
Q 23-512  T -489  ☑ -489 
Q 68-449  T -381  ☑ -381 
Q 117-595 T -478  ☑ -478 
Q 24-758  T -734  ☑ -734 
Q 389-574 T -185  ☑ -185 
Q 277-797 T -520  ☑ -520 
Q 73-290  T -217  ☑ -217 
Q 842-300 T 542   ☑ 542  
Q 965-864 T 101   ☑ 101  
Q 994-79  T 915   ☑ 915  
Q 670-360 T 310   ☑ 310  
Q 521-907 T -386  ☑ -386 
Q 298-37  T 261   ☑ 261  
Q 446-882 T -436  ☑ -436 
Q 713-62  T 651   ☑ 651  
Q 161-745 T -584  ☑ -584 
Q 984-256 T 728   ☑ 728  
Q 48-113  T -65   ☑ -65  
Q 409-4   T 405   ☑ 405  
Q 341-791 T -450  ☑ -450 
Q 828-25  T 

Q 64-35   T 29    ☑ 29   
Q 57-580  T -523  ☑ -523 
Q 487-281 T 206   ☑ 206  
Q 19-133  T -114  ☑ -114 
Q 200-517 T -317  ☑ -317 
Q 895-567 T 328   ☒ 329  
Q 59-136  T -77   ☑ -77  
Q 358-77  T 281   ☑ 281  
Q 71-844  T -773  ☑ -773 
Q 281-391 T -110  ☒ -100 
Q 24-556  T -532  ☑ -532 
Q 143-31  T 112   ☒ 113  
Q 96-307  T -211  ☑ -211 
Q 532-444 T 88    ☑ 88   
Q 839-45  T 794   ☑ 794  
Q 336-11  T 325   ☑ 325  
Q 74-317  T -243  ☑ -243 
Q 591-738 T -147  ☑ -147 
Q 57-433  T -376  ☑ -376 
Q 59-313  T -254  ☑ -254 
Q 95-256  T -161  ☑ -161 
Q 388-741 T -353  ☑ -353 
Q 202-392 T -190  ☑ -190 
Q 998-39  T 959   ☑ 959  
Q 722-14  T 708   ☑ 708  
Q 117-14  T 103   ☑ 103  
Q 791-81  T 710   ☑ 710  
Q 921-921 T 0     ☒ -8   
Q 965-5   T 960   ☑ 960  
Q 634-822 T -188  ☑ -188 
Q 806-378 T 428   ☑ 428  
Q 917-20  T 897   ☑ 897  
Q 396-34  T 362   ☑ 362  
Q 306-140 T 166   ☑ 166  
Q 964-96  T 868   ☒ 878  
Q 952-402 T 550   ☑ 550  
Q 251-677 T -426  ☑ -426 
Q 973-993 T -20   ☒ -10  
Q 676-71  T 

Q 711-504 T 207   ☑ 207  
Q 52-818  T -766  ☑ -766 
Q 821-196 T 625   ☑ 625  
Q 44-988  T -944  ☑ -944 
Q 188-484 T -296  ☒ -396 
Q 905-6   T 899   ☒ 990  
Q 735-80  T 655   ☑ 655  
Q 420-459 T -39   ☑ -39  
Q 424-0   T 424   ☑ 424  
Q 269-59  T 210   ☑ 210  
Q 686-329 T 357   ☑ 357  
Q 603-743 T -140  ☑ -140 
Q 284-889 T -605  ☑ -605 
Q 424-160 T 264   ☑ 264  
Q 896-251 T 645   ☑ 645  
Q 363-21  T 342   ☑ 342  
Q 775-196 T 579   ☒ 589  
Q 72-798  T -726  ☑ -726 
Q 382-26  T 356   ☑ 356  
Q 810-6   T 804   ☑ 804  
Q 111-636 T -525  ☑ -525 
Q 880-188 T 692   ☒ 691  
Q 493-3   T 490   ☑ 490  
Q 543-261 T 282   ☑ 282  
Q 544-394 T 150   ☒ 130  
Q 884-798 T 86    ☒ 97   
Q 45-731  T -686  ☑ -686 
Q 92-33   T 59    ☒ 58   
Q 999-528 T 471   ☑ 471  
Q 258-248 T 10    ☒ 1    
Q 557-33  T 524   ☑ 524  
Q 921-1   T 920   ☑ 920  
Q 598-832 T -234  ☑ -234 
Q 570-936 T -366  ☑ -366 
Q 707-413 T 294   ☑ 294  
Q 741-260 T 481   ☑ 481  
Q 230-68  T 162   ☑ 162  
Q 95-285  T -190  ☒ -180 
Q 29-626  T 

...

Q 463-21  T 442   ☑ 442  
Q 834-12  T 822   ☑ 822  
Q 69-566  T -497  ☑ -497 
Q 363-796 T -433  ☑ -433 
Q 669-76  T 593   ☑ 593  
Q 114-99  T 15    ☒ 25   
Q 322-614 T -292  ☑ -292 
Q 493-67  T 426   ☑ 426  
Q 116-954 T -838  ☑ -838 
Q 701-579 T 122   ☑ 122  
Q 930-808 T 122   ☑ 122  
Q 922-943 T -21   ☒ -31  
Q 133-92  T 41    ☑ 41   
Q 185-301 T -116  ☑ -116 
Q 897-48  T 849   ☑ 849  
Q 84-168  T -84   ☑ -84  
Q 637-955 T -318  ☑ -318 
Q 422-822 T -400  ☒ -490 
Q 35-401  T -366  ☑ -366 
Q 83-442  T -359  ☒ -369 
Q 931-311 T 620   ☒ 610  
Q 161-119 T 42    ☒ 32   
Q 351-45  T 306   ☑ 306  
Q 384-24  T 360   ☑ 360  
Q 588-289 T 299   ☑ 299  
Q 74-453  T -379  ☑ -379 
Q 245-113 T 132   ☑ 132  
Q 188-970 T -782  ☑ -782 
Q 528-2   T 526   ☑ 526  
Q 544-186 T 358   ☑ 358  
Q 231-791 T -560  ☑ -560 
Q 835-506 T 329   ☑ 329  
Q 746-51  T 695   ☑ 695  
Q 172-78  T 94    ☒ 93   
Q 16-390  T -374  ☑ -374 
Q 39-34   T 5     ☒ 2    
Q 61-602  T -541  ☑ -541 
Q 4-47    T -43   ☑ -43  
Q 336-17  T 

Q 583-754 T -171  ☑ -171 
Q 755-723 T 32    ☑ 32   
Q 715-36  T 679   ☑ 679  
Q 508-341 T 167   ☑ 167  
Q 76-778  T -702  ☑ -702 
Q 427-337 T 90    ☑ 90   
Q 701-320 T 381   ☒ 371  
Q 727-799 T -72   ☑ -72  
Q 73-216  T -143  ☑ -143 
Q 207-10  T 197   ☑ 197  
Q 196-380 T -184  ☒ -174 
Q 28-831  T -803  ☑ -803 
Q 297-189 T 108   ☑ 108  
Q 39-730  T -691  ☑ -691 
Q 5-10    T -5    ☒ -9   
Q 828-517 T 311   ☑ 311  
Q 272-2   T 270   ☑ 270  
Q 209-68  T 141   ☑ 141  
Q 369-73  T 296   ☑ 296  
Q 83-549  T -466  ☑ -466 
Q 774-458 T 316   ☑ 316  
Q 191-3   T 188   ☑ 188  
Q 822-789 T 33    ☑ 33   
Q 608-2   T 606   ☑ 606  
Q 161-831 T -670  ☑ -670 
Q 61-46   T 15    ☒ 16   
Q 612-132 T 480   ☑ 480  
Q 371-21  T 350   ☑ 350  
Q 689-630 T 59    ☒ 49   
Q 874-687 T 187   ☑ 187  
Q 695-983 T -288  ☑ -288 
Q 81-329  T -248  ☑ -248 
Q 250-426 T -176  ☑ -176 
Q 329-113 T 216   ☒ 226  
Q 47-240  T -193  ☑ -193 
Q 882-337 T 545   ☑ 545  
Q 840-87  T 753   ☑ 753  
Q 920-70  T 850   ☒ 840  
Q 13-974  T 

Q 68-800  T -732  ☑ -732 
Q 863-623 T 240   ☑ 240  
Q 141-956 T -815  ☑ -815 
Q 906-748 T 158   ☑ 158  
Q 818-9   T 809   ☑ 809  
Q 923-276 T 647   ☑ 647  
Q 293-68  T 225   ☑ 225  
Q 370-448 T -78   ☑ -78  
Q 717-243 T 474   ☑ 474  
Q 702-573 T 129   ☒ 139  
Q 220-53  T 167   ☑ 167  
Q 26-923  T -897  ☑ -897 
Q 624-147 T 477   ☑ 477  
Q 398-559 T -161  ☑ -161 
Q 725-99  T 626   ☑ 626  
Q 318-173 T 145   ☑ 145  
Q 593-53  T 540   ☑ 540  
Q 120-22  T 98    ☑ 98   
Q 25-163  T -138  ☑ -138 
Q 917-32  T 885   ☑ 885  
Q 547-230 T 317   ☑ 317  
Q 76-308  T -232  ☑ -232 
Q 19-447  T -428  ☑ -428 
Q 522-900 T -378  ☑ -378 
Q 598-141 T 457   ☑ 457  
Q 978-115 T 863   ☑ 863  
Q 329-79  T 250   ☑ 250  
Q 896-42  T 854   ☑ 854  
Q 837-822 T 15    ☑ 15   
Q 381-867 T -486  ☑ -486 
Q 90-52   T 38    ☒ 48   
Q 576-275 T 301   ☒ 201  
Q 12-43   T -31   ☑ -31  
Q 24-421  T -397  ☑ -397 
Q 858-11  T 847   ☑ 847  
Q 5-6     T -1    ☒ 0    
Q 922-419 T 503   ☑ 503  
Q 31-447  T -416  ☑ -416 
Q 760-32  T 

Q 147-414 T -267  ☑ -267 
Q 0-52    T -52   ☒ -53  
Q 487-100 T 387   ☑ 387  
Q 254-74  T 180   ☑ 180  
Q 792-44  T 748   ☑ 748  
Q 29-684  T -655  ☑ -655 
Q 34-694  T -660  ☑ -660 
Q 114-296 T -182  ☑ -182 
Q 45-34   T 11    ☒ 10   
Q 590-67  T 523   ☑ 523  
Q 53-707  T -654  ☑ -654 
Q 515-76  T 439   ☑ 439  
Q 903-660 T 243   ☑ 243  
Q 139-44  T 95    ☒ 96   
Q 797-486 T 311   ☑ 311  
Q 554-530 T 24    ☑ 24   
Q 332-236 T 96    ☑ 96   
Q 2-985   T -983  ☑ -983 
Q 235-200 T 35    ☒ 45   
Q 89-100  T -11   ☑ -11  
Q 56-595  T -539  ☑ -539 
Q 524-495 T 29    ☑ 29   
Q 31-184  T -153  ☑ -153 
Q 837-532 T 305   ☑ 305  
Q 76-20   T 56    ☑ 56   
Q 65-628  T -563  ☑ -563 
Q 336-860 T -524  ☑ -524 
Q 513-905 T -392  ☒ -382 
Q 93-606  T -513  ☑ -513 
Q 970-14  T 956   ☑ 956  
Q 291-246 T 45    ☑ 45   
Q 238-344 T -106  ☑ -106 
Q 788-152 T 636   ☑ 636  
Q 247-46  T 201   ☑ 201  
Q 909-328 T 581   ☑ 581  
Q 71-967  T -896  ☑ -896 
Q 938-82  T 856   ☑ 856  
Q 68-47   T 21    ☑ 21   
Q 911-687 T 

Q 5-100   T -95   ☑ -95  
Q 701-635 T 66    ☑ 66   
Q 199-36  T 163   ☑ 163  
Q 632-484 T 148   ☑ 148  
Q 0-749   T -749  ☑ -749 
Q 11-230  T -219  ☑ -219 
Q 964-5   T 959   ☒ 969  
Q 513-6   T 507   ☑ 507  
Q 68-485  T -417  ☑ -417 
Q 514-85  T 429   ☑ 429  
Q 412-56  T 356   ☑ 356  
Q 143-69  T 74    ☑ 74   
Q 14-352  T -338  ☑ -338 
Q 706-47  T 659   ☒ 669  
Q 76-664  T -588  ☑ -588 
Q 82-357  T -275  ☑ -275 
Q 318-296 T 22    ☒ 21   
Q 96-428  T -332  ☑ -332 
Q 439-712 T -273  ☑ -273 
Q 623-92  T 531   ☑ 531  
Q 66-437  T -371  ☑ -371 
Q 651-632 T 19    ☒ 29   
Q 594-21  T 573   ☑ 573  
Q 172-17  T 155   ☑ 155  
Q 838-869 T -31   ☑ -31  
Q 278-758 T -480  ☑ -480 
Q 833-130 T 703   ☑ 703  
Q 45-83   T -38   ☑ -38  
Q 790-109 T 681   ☑ 681  
Q 304-791 T -487  ☑ -487 
Q 754-5   T 749   ☑ 749  
Q 109-19  T 90    ☑ 90   
Q 981-32  T 949   ☑ 949  
Q 314-931 T -617  ☑ -617 
Q 479-987 T -508  ☑ -508 
Q 72-601  T -529  ☑ -529 
Q 73-835  T -762  ☑ -762 
Q 92-905  T -813  ☑ -813 
Q 554-12  T 